# Data Analysis in DuckDB Courselet

**Authors:** 
 - David Koop (dakoop@niu.edu)

**Last Updated:** 2025-09-20

This courselet provides background information on using the DuckDB database in python. It focuses on operations designed to wrangle data but includes a number of details on using DuckDB to load, structure, and query data. There are exercises throughout as well as a challenging final part to test your skills. We will use the City of Chicago's [Food Inspection Data](https://data.cityofchicago.org/Health-Human-Services/Food-Inspections/4ijn-s7e5) for this courselet.

This first cell loads a specific subset of data from the food inspection data.

In [ ]:
# Changing the way the jupyter files react to expressions hence displaying the last assigned value in the cell.
%config InteractiveShell.ast_node_interactivity = 'last_expr_or_assign'

In [ ]:
# This segment is used to download the ZIP file of the dataset from online source.

import urllib.request
import gzip

url = "https://data.cityofchicago.org/resource/4ijn-s7e5.csv?"
params = {
    "$where": "2000000 <= inspection_id AND inspection_id <= 2500000",
    "$limit": "100000",
}
encoded_params = urllib.parse.urlencode(params)
# print(url + encoded_params)
request = urllib.request.Request(url + encoded_params)
request.add_header("accept-encoding", "gzip")
with urllib.request.urlopen(request) as response:
    if response.info().get("Content-Encoding") == "gzip":
        with open("Food_Inspections.csv.gz", "wb") as f:
            f.write(response.read())
    else:
        with gzip.open("Food_Inspections.csv.gz", "wb") as f:
            f.write(response.read())

### Reading Data

DuckDB has a number of way to read data, supporting a variety of data formats. Some of the most frequently used methods are 

- `read_csv` - Reads Comma Separated Values which is text data that where attributes are separated by commas. When necessary, each attribute is enclosed by a double quotes. Because this is a text-based format, there is no type information provided.

- `read_json` - JavaScript Object Notation (JSON) is a textual format that mimics the specification of nested objects and lists in JavaScript, but limits values to literals. While it does not store type information, it can be paired with a schema and some information can be inferred from the representation (numeric values are specified differently than strings of digits, for example)

- `read_parquet` - Apache parquet is a open-source column oriented data storage format. The `read_parquet` function allows users to read from this format.

- `read_xlsx` - Reads MS Office Spreadsheets. It only reads the newer xlsx format, not the xls format.

DuckDB can read some compressed formats, including gzipped csv files, without the need to first decompress them.

First, we need to import the `duckdb` library. Then, we will create an im-memory database. Finally, we can read the Chicago Food Inspections data directly using the `read_csv` method and its support for gzipped files.

In [ ]:
import duckdb

con = duckdb.connect() # by default, uses an in-memory database
con.sql("SELECT * FROM read_csv('Food_Inspections.csv.gz')")

The output is table but it also looks similar to a dataframe. It may als remind you of a sheet from a spreadsheet program. The header rows show the name of each column and its type. This is followed by a subset of the rows, typically the first and last ten rows. Finally, it shows the number of rows, but depending on how much has been loaded, this may be a `?` indicating that not all rows have been loaded.  Since we plan to use this table througout this courselet, we can create a table in our database for it.

In [ ]:
con.sql("CREATE TABLE insp AS SELECT * FROM read_csv('Food_Inspections.csv.gz')")

Now, we can display this table using a standard SELECT query as before. 

In [ ]:
con.sql("SELECT * FROM insp").show()

We can also use the `table` method to access the table directly, and we can display the tables as dataframes using the `df` or `pl` methods. Note that this may take longer because it requires loaded the entire table.

In [ ]:
con.table('insp').df()

In [ ]:
con.table('insp').pl()

We will use the polars output display for this courselet but you may choose to use `show` or `df` instead. Now, we can extract a single column from the table using the standard SQL syntax.

In [ ]:
con.query('SELECT dba_name FROM insp').pl()

##### Exercise

You can select multiple columns at once by passing a comma-separated list to the `SELECT` method. Try extracting both the `dba_name` column and the `results` column.

In [ ]:
# Your code here

##### Solution

In [ ]:
con.sql("SELECT dba_name, results FROM insp").pl()

### Extracting Data Items

DuckDB supports row access, but it is not designed to process items row by row. **Try to avoid iterating through items**! You can access a single row using the `fetchone()` method and multiple rows using the `fetchmany` method. These are returned as tuples.

In [ ]:
con.sql("SELECT * FROM insp").fetchone()

In [ ]:
con.execute("SELECT * FROM insp").fetchmany(5)

Alternatively, you can use the `LIMIT` clause in a SQL query to return a specific number of rows, and `OFFSET` to skip a specific number of rows. However, there is no guarantee that these rows will be returned in the order you expect unless you use a specific `ORDER BY` clause.

In [ ]:
con.sql("SELECT * FROM insp LIMIT 5 OFFSET 10").pl()

If `insp` were a dataframe, this would be similar to the slicing expression`insp[10:15]`.

#### Indexing

As mentioned earlier, there is no explicit index for a row in a duckdb table in constrast to pandas. However, you could add a unique integer identifier column to your table if you wish using `row_number|`. This is not generally necessary and can clutter your dataframe.

In [ ]:
con.sql("SELECT row_number() OVER () AS idx, * FROM insp").pl()

### Inspecting Databases

While looking at individual rows or slices of a table can be helpful, there are also methods to understand the structure of a table or provide an overview. DuckDB provides the column names in its output, but we can also access these column_name list directly from the information_schema. We can also use the `DESCRIBE` statement or `table_info` pragma method to include type information as well as details on whether the column can be null and if it is part of the primary key.

In [ ]:
con.sql("""SELECT column_name FROM information_schema.columns
WHERE table_name = 'insp'
ORDER BY ordinal_position""").pl()

In [ ]:
con.sql("DESCRIBE insp").pl()

In [ ]:
con.sql("PRAGMA table_info('insp')").pl()

Like dataframes, each column in a DuckDB table has a data *type*. For numeric types, we have float and int variants using different numbers of bits (e.g. `BIGINT` or `DOUBLE`), but duckdb also supports dates, datetimes, strings, and categorical types. You can query the information schema or table_info results for a particular column's type.

In [ ]:
con.sql("""SELECT data_type FROM information_schema.columns
WHERE table_name = 'insp' AND column_name == 'longitude'""").pl()


Note that DuckDB will balk at mixed types in a table, requiring explicit casting to a common type.

In [ ]:
con.sql("SELECT * FROM VALUES ('a'), (12), (34.5) AS t(name)").pl()

### Table Overview

While the standard table output is often good enough to undersand the contents of the table and see example values, `SUMMARIZE` gives an overview of the values in the table.

In [ ]:
con.sql("SUMMARIZE insp").pl()

Notice that there are a number of different statistics that are calculated, but some only apply to numeric columns, meaning that non-numeric columns have null entries for quartiles (`q*`), `avg`, and standard deviation (`std`). In addition, this is meant for presentation as the types for these columns are `VARCHAR` (string) types.

### Modifying the Schema

In some cases, we may wish to update the schema by changing either the names or types of columns. Renaming columns can be done using the `RENAME COLUMN` clause with an `ALTER TABLE` statement.

In [ ]:
con.sql("ALTER TABLE insp RENAME COLUMN license_ TO license")
con.table('insp').pl()

We can also convert between types when appropriate using `CAST` method or using the `::` shorthand. For example, we can cast a column `license` to an unsigned integer using `CAST(license AS UINT)` or `license::UINT`.

In [ ]:
con.sql("SELECT CAST(license AS UINT64) AS license FROM insp").show()

In [ ]:
con.sql("SELECT license::UINT64 FROM insp").show()

##### Exercise

Try converting the `zip` and `violations` columns to the `Int32` type. Your code should not work--that's ok. Why do you think this happens? Does one of the columns succeed?

In [ ]:
# Your code here

##### Solution

In [ ]:
con.sql("SELECT CAST(zip AS INT32), CAST(violations AS INT32) FROM insp").pl()

We can see that it is not possible to convert many of the violation strings to integers.

In [ ]:
con.sql("SELECT CAST(zip AS INT32) FROM insp").pl()

### Nullable Types

By default, columns in DuckDB are nullable, but it is possible to set them to be non-nullable when defining the schema or using . Thus, even though `license` is an integer, there are three null values in that column. 

In [ ]:
con.sql("SELECT COUNT(*) FROM insp WHERE license IS NULL").pl()

You can alter a column to make it non-nullable, but you must set any existing null values to a non-null value first.

In [ ]:
con.sql("ALTER TABLE insp ALTER COLUMN license SET NOT NULL")

In [ ]:
con.sql("UPDATE insp SET license = -1 WHERE license IS NULL")
con.sql("ALTER TABLE insp ALTER COLUMN license SET NOT NULL")

### Timestamps

DuckDB also supports datetime values. There are a number of formats for dates and times, and DuckDB can convert well-structured strings to `TIMESTAMP` types automatically using casting. In other cases, you may need to call `strptime` methods with the proper format string. DuckDB uses the format string specifiers from C documented [here](https://duckdb.org/docs/stable/sql/functions/dateformat#format-specifiers). In our data, the read_csv method already automatically converted the inspection_date column to a timestamp, but if we override that, we can cast it ourselves.

In [ ]:
con.sql("CREATE TABLE insp_no_ts AS SELECT * from read_csv('Food_Inspections.csv.gz', types={'inspection_date': 'VARCHAR'})")
con.table('insp_no_ts').pl()

In [ ]:
con.table('insp_no_ts').pl()

In [ ]:
con.sql("SELECT CAST(inspection_date AS TIMESTAMP) AS inspection_date FROM insp").pl()

In [ ]:
con.sql("SELECT strptime(inspection_date, '%Y-%m-%dT%H:%M:%S.%f') AS inspection_date FROM insp_no_ts").pl()

### Updating Tables

To update a table with new columns, we generally create a new table using `CREATE TABLE AS SELECT ...` syntax. This allows us to create a new table with the desired columns and types. We can then drop the old table and rename the new table to the original name if desired.

In [ ]:
con.sql("CREATE TABLE insp_updated AS SELECT * EXCLUDE (inspection_date), CAST(inspection_date AS TIMESTAMP) AS inspection_date FROM insp_no_ts")

In [ ]:
con.table("insp_updated").pl()

This method creates a **new** table. We could also rename the new column using the `AS` clause in order to keep the original name.

In [ ]:
con.sql("CREATE TABLE insp_updated2 AS SELECT *, CAST(inspection_date AS TIMESTAMP) AS inspection_date_dt FROM insp_no_ts")

In [ ]:
con.table('insp_updated2').pl()

### Derived Data

In addition to converting columns, we can also create new columns from existing columns via operations. For example, we might wish to construct an `full_address` column that combines the `address`, `city`, `state`, and `zip` columns. In this case, `||` functions as concatenation. For numeric columns, we could use other arithmetic operators to compute derived columns.

In [ ]:
con.sql("SELECT address || '\n' || city || ', ' || state || ' ' || zip AS full_address FROM insp").pl()

To addd this column to our existing table, we can run an `ALTER TABLE ... ADD COLUMN` statement along with an `UPDATE` statement to populate the new column.

In [ ]:
con.sql("ALTER TABLE insp ADD COLUMN full_name VARCHAR")
con.sql("UPDATE insp SET full_name = address || '\n' || city || ', ' || state || ' ' || zip")
con.table('insp').pl()

### Queries

With some initial processing completed, we can begin our analysis of the data. We can filter our table to those values that match particular criteria using the `WHERE` clause. For example, if we want to find all the inspections that were given a pass, we could do that with the boolean expression `results == 'Pass'`.

In [ ]:
con.sql("SELECT * FROM insp WHERE results == 'Pass'").pl()

### Boolean Comparators & Operators

Suppose we are interested in all the inspections that received a pass in the 60608 zip code. Python's normal comparators (`>`, `<`, `>=`, `<=`, `==`, `!=`) can be used directly in SQL expressions. In addition, `AND`, `OR`, and `NOT` function as the logical operators to connect comparisons.

In [ ]:
con.sql("SELECT * FROM insp WHERE results == 'Pass' AND zip == 60608").pl()

##### Exercise

Find all inspections that received a `"Pass"` or `"Pass w/ Conditions"` and were not "Restaurant" facilities.

In [ ]:
# Your code here

##### Solution



In [ ]:
con.sql("SELECT * FROM insp WHERE (results == 'Pass' OR results == 'Pass w/ Conditions') AND NOT (facility_type == 'Restaurant')").pl()

### Group By

In order to analyze the results, it can be useful to not only filter them but also to group them. If we want to count the number of inspection results of each type, we can use the `COUNT` method coupled with a `GROUP BY` clause:

In [ ]:
con.sql("SELECT results, COUNT(*) FROM insp GROUP BY results").pl()

This returns a table with the results as one column and the count as the other. Note that this is not sorted by default, but we can use the `ORDER BY` clause to recitfy that.

In [ ]:
con.sql("SELECT results, COUNT(*) FROM insp GROUP BY results ORDER BY COUNT(*) DESC").pl()

##### Exercise

Write a query to count by both the `inspection_type` and `results`?

##### Solution

In [ ]:
con.sql("SELECT inspection_type, results, COUNT(*) FROM insp GROUP BY inspection_type, results").pl()

#### Aggregations

Counting can help in some cases, but we might want to perform some statistics on the columns as well. This dataset doesn't have a lot of quantitative values, but the `inspection_date` is one that we can use. For example, we might compute the mean inspection date for a given zip code. To to this, we use `GROUP BY` clause with different aggregate functions.

Some common aggregation functions are: 
- `COUNT()` (count of how many items are in the group)
- `SUM()`
- `MIN()` and `MAX()`
- `MEAN()`
- `MEDIAN()`
- `STDDEV()` (standard deviation)
- `VAR()` (variance)

In [ ]:
con.sql("SELECT zip, MEAN(inspection_date) FROM insp GROUP BY zip").pl()

This isn't all that useful on its own, however, because we don't know if those zip codes that seemingly aren't inspected often or are typos or devoid of food establishments. We'd like to have both the mean and the count. We can add a second expression to the our `SELECT` clause and then order the final result by the number of results.

In [ ]:
con.sql("SELECT zip, MEAN(inspection_date), COUNT(*) FROM insp GROUP BY zip ORDER BY COUNT(*) DESC").pl()

We could also include the maximum inspection date from this part of the dataset:

In [ ]:
con.sql("SELECT zip, MEAN(inspection_date), MAX(inspection_date), COUNT(*) FROM insp GROUP BY zip ORDER BY COUNT(*) DESC").pl()

Note that DuckDB automatically renames the columns based on the operation, but we can use the `AS` clause to rename them.

In [ ]:
con.sql("SELECT zip, MEAN(inspection_date) AS mean_inspection_date, MAX(inspection_date) AS max_inspection_date, COUNT(*) AS count FROM insp GROUP BY zip ORDER BY count DESC").pl()

If you wish to see all possible values for a group, the `LIST` aggregation can be used.Here, we also use an *expression* to construct the group by by extracting the year from the inspection date.

In [ ]:
con.sql("""SELECT
    EXTRACT(YEAR FROM inspection_date) AS inspection_year,
    LIST(results) AS results
    FROM insp
    WHERE license = 2517129
    GROUP BY inspection_year
    ORDER BY inspection_year
""").pl()

##### Exercise

For each year starting in 2019, find the number of facilities for each risk level that passed with conditions. Ignore those risk levels that do not start with the text `"Risk"`

In [ ]:
# Your code here

##### Solution

In [ ]:
con.sql("""SELECT
    EXTRACT(YEAR FROM inspection_date) AS inspection_year,
    risk,
    COUNT(results) AS results
    FROM insp
    WHERE starts_with(risk, 'Risk') AND inspection_year >= 2019
    GROUP BY inspection_year, risk
    ORDER BY inspection_year, risk
""").pl()

### String Processing

A key feature of DuckDB is its ability to apply [text functions](https://duckdb.org/docs/stable/sql/functions/text) to entire columns. Some of these methods align with methods that exist for python string objects while others integrate functionality offered by regular expressions.

If we just search for locations named `"McDonald's"`, we find far fewer inspections than we would expect.

In [ ]:
con.sql("SELECT * FROM insp WHERE dba_name = 'McDonald''s'").pl()

Looking back at the dataset, you might notice that the names of establishments are generally in all caps. We can match against the captialized version by transforming all of the names to uppercase using the `upper` method.

In [ ]:
con.sql("SELECT * FROM insp WHERE upper(dba_name) = 'MCDONALD''S'").pl()

That's better but still seems like too few results over an almost four-year period. This might be because there are extra characters in the name (e.g. "McDonald's #11290" or "McDonald's Restaurant"). The `LIKE` operator will allow us to match McDonald's anywhere in the string and we can use `upper` to ignore casing.

In [ ]:
con.sql("SELECT * FROM insp WHERE upper(dba_name) LIKE '%MCDONALD''S%'").pl()

Now, we might wonder if there are some locations where the apostrophe is dropped (McDonalds). In this case, we could search for those specifically, but we could also create a **regular expression** that specifies the possibility--but not requirement--of an apostrophe. Learning regular expressions takes some time, but mastering them provides important tools for pattern matching. Even if you have used them, a reference for all of the special characters can be useful. *Note:* DuckDB uses the RE2 library which is similar to python's `re` library but has a few less advanced featurues. See the [RE2 documentation](https://github.com/google/re2/wiki/Syntax). For us, `'?` indicates that there exist zero or one apostrophe between final 'd' and 's', and `(?i)` sets the case-insensitive flag. We use the `regexp_matches` method for regular expression searches.

In [ ]:
con.sql("SELECT * FROM insp WHERE regexp_matches(dba_name, '(?i)mcdonald''?s')").pl()

We can count how many times each version of the name is used using a `GROUP BY` query, but we can also look at the number of unique names using the `DISTINCT` modifier.

In [ ]:
con.sql("CREATE TABLE mcds AS SELECT * FROM insp WHERE regexp_matches(dba_name, '(?i)mcdonald''?s')")
con.sql("SELECT dba_name, COUNT(*) FROM mcds GROUP BY dba_name ORDER BY COUNT(*) DESC").pl()

In [ ]:
con.sql("SELECT COUNT(DISTINCT dba_name) FROM mcds").pl()

### Data Transformation

A key component of a failed inspection is understanding the types of violations that the inspector found. In our data, this is all packed into the `violations` column. Let's look at this string from a specific inspection using the textwrap module to break up the long string.

In [ ]:
import textwrap

textwrap.wrap(con.sql("SELECT violations FROM insp WHERE inspection_id = 2498181").fetchone()[0])

##### Exercise

Try to determine what the format of the violations string is by looking at other examples. First, think about how you might find inspections that have violations and then look at a few of them to see if you can observe a pattern.

##### Solution

We can use a query to find inspections where the results was "Fail" or look for inspections where the violations column is not empty.

In [ ]:
con.sql("SELECT violations FROM insp WHERE results = 'Fail'").pl()

In [ ]:
con.sql("SELECT violations FROM insp WHERE results = 'Fail' AND violations IS NOT NULL").pl()

In [ ]:
textwrap.wrap(con.sql("SELECT violations FROM insp WHERE results = 'Fail' AND violations IS NOT NULL").fetchone()[0])

After examining a few of these, we might notice that there seems to be a pattern where there are a numbered rules, where each is followed by a dash and then comments about how the rule was violated, and rules are separated by the `|` symbol.

#### More String Methods

With this in mind, we can use some string methods that expand a string to a list of strings. The `string_split` method does just that for a given delimiter.

In [ ]:
con.sql("SELECT string_split(violations, '|') AS violations FROM insp").pl()

Now each entry in our column is a (possibly null) list of strings. If our goal is to analyze the types of violations, we might wish to separate the individual violations out into the violation number, the violation text, and the comments about the violation. The first step is to separate the violations. We can use the `UNNEST` method to separate each violation into a new row. We will create this as new view in the database so we don't have to keep copying and pasting this code.

In [ ]:
con.sql("CREATE VIEW violations AS SELECT UNNEST(string_split(violations, '|')) AS violations FROM insp")
con.table('violations').pl()

Now, our goal is to separate each of these into the three pieces of information:

1. violation number
2. violation text
3. comments

Let's start with the violation number. It is a number followed by a dot. we could potentially use that dot to split the string again. We'd only want to split **once** however so we have to join the rest of the array back together. 

In [ ]:
con.sql("""SELECT
    arr[1] AS violation_number,
    ARRAY_TO_STRING(arr[2:], '.') AS rest
FROM (
    SELECT string_split(violations, '.') AS arr
    FROM violations
)
""").pl()

##### Exercise

Convert the violation number to an integer. Note that you will have to find a way to strip the whitespace from the beginning of the strings. Also strip the whitespace from the other column.

In [ ]:
# Your code here

##### Solution

In [ ]:
con.sql("""SELECT
    CAST(TRIM(arr[1]) as INT) AS violation_number,
    TRIM(ARRAY_TO_STRING(arr[2:], '.')) AS rest
FROM (
    SELECT string_split(violations, '.') AS arr
    FROM violations
)
""").pl()

#### Back to Regular Expressions

Another string method that polars has related to regular expressions is the `regexp_extract` method. We could have used it to construct a pattern to extract the violation number instead. The parentheses indicate the portion of the pattern we wish to capture, and the final argument is the group we wish to extract (starting with 1).

In [ ]:
con.sql(r"SELECT regexp_extract(UNNEST(string_split(violations, '|')), '^\s*(\d+)\.', 1) AS violation_number FROM insp").pl()

These can be converted to integers immediately since we did not include the spaces in our extraction.

In [ ]:
con.sql(r"SELECT CAST(regexp_extract(UNNEST(string_split(violations, '|')), '^\s*(\d+)\.', 1) AS INT) AS violation_number FROM insp").pl()

We can use this this strategy to extract both parts of the regular expression. Now, we can ask for the groups individually and name them. This creates a struct.

In [ ]:
con.sql(r"""SELECT regexp_extract(UNNEST(string_split(violations, '|')), '(\d+)\.\s*(.*)', ['violation_number','rest']) AS vstruct FROM insp""").pl()

In [ ]:
con.sql(r"""CREATE VIEW violations_struct AS SELECT regexp_extract(UNNEST(string_split(violations, '|')), '(\d+)\.\s*(.*)', ['violation_number','rest']) AS vstruct FROM insp""")
con.table('violations_struct').pl()

Now we can extract the parts of the struct and cast cast the violation number to an integer.

In [ ]:
con.sql(r"""SELECT CAST(struct_extract(vstruct, 'violation_number') AS INT) AS violation_number, 
        struct_extract(vstruct, 'rest') as rest
        FROM violations_struct""").pl()

### Final Exercises

1. All right, we've started attacking our problem but we haven't finished it. It's now up to you to extract all three columns (violation_num, violation_text, comments) for all of the violations. Be careful. A few violations have no comments.

2. Now, determine which violation is **most frequent**. But before you do that, note that the violation numbers changed at some point in the past. Read through the [metadata](https://data.cityofchicago.org/Health-Human-Services/Food-Inspections/4ijn-s7e5/about_data) to learn more. So you will need to split the violations into two groups and find the most frequent one across both groups.